In [7]:
# Import
import pandas
import re
# Alignement 
import nltk
import codecs
import gensim
from scipy import sparse
import itertools
from sklearn.feature_extraction.text import CountVectorizer ,TfidfTransformer
import scipy.sparse
import scipy.io
from sklearn import preprocessing
from keras.models import Sequential
from keras.layers.core import Dense, Dropout, Activation,AutoEncoder
from keras.optimizers import SGD
from keras.layers import containers
from mlp import *
import mlp
import sklearn.metrics
import shelve
import pickle
from collections import Counter
import sys
%matplotlib inline

In [8]:
import gensim

ImportError: cannot import name interfaces

In [4]:
ASR={}
TRS={}
ASR["TRAIN"]=pandas.read_table("./ASR/corpus_TRAIN_ASR.srl",sep="\t",header=None,na_values=None,keep_default_na=False)
ASR["DEV"]=pandas.read_table("./ASR/corpus_DEV_ASR.srl",sep="\t",header=None,na_values=None,keep_default_na=False)
ASR["TEST"]=pandas.read_table("./ASR/corpus_TEST_ASR.srl",sep="\t",header=None,na_values=None,keep_default_na=False)

TRS["TRAIN"]=pandas.read_table("./TRS/corpus_TRAIN_TRS.srl",sep="\t",header=None,na_values=None,keep_default_na=False)
TRS["DEV"]=pandas.read_table("./TRS/corpus_DEV_TRS.srl",sep="\t",header=None,na_values=None,keep_default_na=False)
TRS["TEST"]=pandas.read_table("./TRS/corpus_TEST_TRS.srl",sep="\t",header=None,na_values=None,keep_default_na=False)


In [251]:
ASR["TRAIN"].head()

0                         1  \
0  DECODA  20101206_RATP_SCD_0424_6   
1  DECODA  20101206_RATP_SCD_0062_1   
2  DECODA  20101206_RATP_SCD_0425_6   
3  DECODA  20091112_RATP_SCD_1209_4   
4  DECODA  20091112_RATP_SCD_1208_4   

                                                   2  
0  là vous répondre  là vous répondre   enfin  ou...  
1  bonsoir  oui bonsoir madame je vous téléphone ...  
2  et vous répondre  voilà  je  sais  et vous rép...  
3  bonsoir  oui bonsoir monsieur bonsoir  bonsoir...  
4  bonjour monsieur écoute hein  bonjour monsieur...

In [309]:
coucou=ASR["TRAIN"].sort_values(by=[1])[1] == TRS["TRAIN"].sort_values(by=[1])[1]

In [314]:
coucou.all(axis=0)

True

In [ ]:
ASR["TRAIN"].sort

In [192]:
tok2 = nltk.RegexpTokenizer(ur"(?u)\w+|\d+(?:[.,]\d+)?(?:\s*%)?|\w'|[^\w\s]",flags=re.UNICODE|re.DOTALL )
#"\d+(\[.,]\d+)?\s*%|\w'|\w+|[^\w\s]"
    #          \d+(\.\d+)?\s*%   # les pourcentages
    #    | \w'               # les contractions d', l', ...
    #    | \w+               # les mots pleins
    #    | [^\w\s]           # les ponctuations
    #  (?:[lcdjmnts]|qu)['’]                         # Contractions
  #      | http:[^\s]+\.\w{2,3}                          # Adresses web
  #      | \d+[.,]\d+                                    # Les réels en/fr
  #      | [.-]+                                         # Les ponctuations
  #      | \w+                                           # Les mots pleins
  #      | [^\w\s] 
def yield_corpus(df_list):
    for corpus in df_list:
        for id,doc in corpus.iterrows():
            try:
                #print doc[2]
                yield tok2.tokenize(doc[2].decode("utf8"))
            except:
                e = sys.exc_info()[0]
                print doc[2],e
                raise
def yield_corpus_wbw(df_list):
    for corpus in df_list:
        for id,doc in corpus.iterrows():
            try:
                 for x in tok2.tokenize(doc[2].decode("utf-8")):
                        yield x.lower()
            except:
                print doc[2]
                raise

In [411]:
vocab1=[x.split(':')[0] for x in codecs.open("./lists_mots/listeMots_300WPT__TRAIN_RES.txt")]
vocab2=[x.split(':')[0] for x in codecs.open("./lists_mots/listeMots_300WPT__TRAIN_TRS.txt")]
vocab3=[x.split(':')[0] for x in codecs.open("./lists_mots/listeMots_300WPT__TRAIN_TRS_RES.txt")]
#vocab3=list(set(vocab1).union(set(vocab2)))

In [386]:
print len(vocab1),len(vocab2),len(vocab3)
print len(set(vocab1).intersection(set(vocab2)))
print len(set(vocab1).union(set(vocab2)))

1310 1439 1432
1031
1718


In [399]:
ASR_count=Counter(yield_corpus_wbw([ASR["TRAIN"]]))

In [412]:
dico=CountVectorizer(binary=True,vocabulary=vocab3)

In [413]:
sparse=shelve.open("Sparse_mat_bin.shelve",writeback=True)
sparse["ASR"]={}
sparse["TRS"]={}
sparse["LABEL"]={}
sparse["LABEL"]["TRAIN"]=ASR["TRAIN"].sort_values(by=[1])[1]
sparse["LABEL"]["DEV"]=ASR["DEV"].sort_values(by=[1])[1]
sparse["LABEL"]["TEST"]=ASR["TEST"].sort_values(by=[1])[1]
for key in ASR.keys():
    sparse["ASR"][key]=dico.transform(ASR[key].sort_values(by=[1])[2])
    sparse["TRS"][key]=dico.transform(TRS[key].sort_values(by=[1])[2])
sparse.sync()
sparse.close()

In [416]:
sparse=shelve.open("Sparse_mat_tfidf.shelve",writeback=True)
sparse["ASR"]={}
sparse["TRS"]={}
sparse["LABEL"]={}
sparse["LABEL"]["TRAIN"]=ASR["TRAIN"].sort_values(by=[1])[1]
sparse["LABEL"]["DEV"]=ASR["DEV"].sort_values(by=[1])[1]
sparse["LABEL"]["TEST"]=ASR["TEST"].sort_values(by=[1])[1]

tf_ASR=TfidfTransformer(norm="l2")
tf_TRS=TfidfTransformer(norm="l2")
tf_TRS.fit(dico2.transform(TRS["TRAIN"].sort_values(by=[1])[2]))
tf_ASR.fit(dico2.transform(ASR["TRAIN"].sort_values(by=[1])[2]))
for key in ASR.keys():
    sparse["ASR"][key]=tf_ASR.transform(dico2.transform(ASR[key].sort_values(by=[1])[2]))
    sparse["TRS"][key]=tf_TRS.transform(dico2.transform(TRS[key].sort_values(by=[1])[2]))

In [417]:
sparse.sync()
sparse.close()

In [11]:
all_vocab=list(set(yield_corpus_wbw([ASR["TRAIN"],TRS["TRAIN"]])))
all_vocab.sort()

In [15]:
all_vocab[10:15]

[u'a4', u'abandonn\xe9', u'abbesses', u'abb\xe9', u'abcd']

In [16]:
dico3=CountVectorizer(binary=True,vocabulary=all_vocab)

In [19]:
sparse=shelve.open("Sparse_mat_bigbin.shelve",writeback=True)
sparse["ASR"]={}
sparse["TRS"]={}
sparse["LABEL"]={}
sparse["LABEL"]["TRAIN"]=ASR["TRAIN"].sort_values(by=[1])[1]
sparse["LABEL"]["DEV"]=ASR["DEV"].sort_values(by=[1])[1]
sparse["LABEL"]["TEST"]=ASR["TEST"].sort_values(by=[1])[1]

tf_ASR=TfidfTransformer(norm="l2")
tf_TRS=TfidfTransformer(norm="l2")
tf_TRS.fit(dico3.transform(TRS["TRAIN"].sort_values(by=[1])[2]))
tf_ASR.fit(dico3.transform(ASR["TRAIN"].sort_values(by=[1])[2]))
for key in ASR.keys():
    sparse["ASR"][key]=tf_ASR.transform(dico3.transform(ASR[key].sort_values(by=[1])[2]))
    sparse["TRS"][key]=tf_TRS.transform(dico3.transform(TRS[key].sort_values(by=[1])[2]))

In [20]:
sparse.sync()
sparse.close()

In [ ]:
sparse=shelve.open("Sparse_mat_bigbin.shelve")